In [1]:
from google.colab import drive
import pandas as pd

drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

# Cargar los datos (enlace:https://insideairbnb.com/get-the-data/)
df = pd.read_csv('/content/drive/My Drive/listings.csv')

In [3]:
import pandas as pd
import plotly.express as px
import folium
from folium.plugins import MarkerCluster
from google.colab import drive
from IPython.display import display

if not pd.io.common.file_exists('/content/drive/My Drive/listings.csv'):
    drive.mount('/content/drive')

try:
    df = pd.read_csv('/content/drive/My Drive/listings.csv')

    # Limpieza
    df['price'] = df['price'].astype(str).str.replace('$', '').str.replace(',', '')
    df['price'] = pd.to_numeric(df['price'], errors='coerce')
    df = df.dropna(subset=['latitude', 'longitude', 'price', 'neighbourhood_group'])
    df = df[df['price'] > 0]

    print(f" Datos listos: {len(df)} registros.")

except Exception as e:
    print(f" Error: {e}")
    df = pd.DataFrame()


#  categoría de precios para simplificar el flujo
def clasificar_precio(p):
    if p < 50: return '1. Económico (<50€)'
    elif p < 100: return '2. Estándar (50-100€)'
    elif p < 200: return '3. Premium (100-200€)'
    else: return '4. Lujo (>200€)'

df['Rango Precio'] = df['price'].apply(clasificar_precio)

#  VISUALIZACIÓN 1: DIAGRAMA DE FLUJO (PARALLEL CATEGORIES)
# Esta visualización muestra las relaciones complejas de un vistazo
print("\nGenerando Diagrama de Flujo Multidimensional...")

fig_parcats = px.parallel_categories(
    df,
    dimensions=['neighbourhood_group', 'room_type', 'Rango Precio'],
    color="price",
    color_continuous_scale=px.colors.sequential.Inferno,
    labels={'neighbourhood_group': 'Distrito', 'room_type': 'Tipo', 'Rango Precio': 'Categoría Precio'},
    title=" Flujo del Mercado: ¿De dónde viene la oferta y cuánto cuesta?",
    height=600
)

# Ajustes estéticos
fig_parcats.update_layout(
    margin=dict(l=20, r=20, t=50, b=20),
    paper_bgcolor="rgb(20, 20, 20)", # Fondo oscuro elegante
    font=dict(color="white")
)
fig_parcats.show()


#  VISUALIZACIÓN: MAPA DE CLÚSTERES
#  mapa estilo "Google Maps" interactivo que agrupa puntos
print("\nGenerando Mapa Interactivo de Clústeres...")

# Centrar el mapa en BCN
mapa = folium.Map(location=[41.39, 2.16], zoom_start=12, tiles='CartoDB dark_matter')

# Crear el grupo de clústeres
marker_cluster = MarkerCluster().add_to(mapa)

# Añadimos solo una muestra (ej. 2000 puntos) para que el mapa vuele y no se trabe
# Priorizamos los que tienen reseñas (son más relevantes)
df_sample = df.sort_values('number_of_reviews', ascending=False).head(2000)

for idx, row in df_sample.iterrows():
    # Color según precio
    color_punto = '#ff4d4d' if row['price'] > 150 else '#4dff88'

    folium.CircleMarker(
        location=[row['latitude'], row['longitude']],
        radius=5,
        popup=f"<b>{row['name']}</b><br>Precio: {row['price']}€<br>Zona: {row['neighbourhood']}",
        color=color_punto,
        fill=True,
        fill_opacity=0.7
    ).add_to(marker_cluster)

display(mapa)

 Datos listos: 15276 registros.

Generando Diagrama de Flujo Multidimensional...



Generando Mapa Interactivo de Clústeres...


In [4]:

import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
from google.colab import drive

if not pd.io.common.file_exists('/content/drive/My Drive/listings.csv'):
    drive.mount('/content/drive')

df = pd.read_csv('/content/drive/My Drive/listings.csv')

# Limpieza rápida
df['price'] = pd.to_numeric(df['price'], errors='coerce')
df = df.dropna(subset=['price', 'latitude', 'longitude', 'neighbourhood_group'])
df = df[df['price'].between(10, 300)] # Filtramos lujo extremo para estética
# Ordenamos por mediana de precio para que el gráfico tenga sentido visual
orden_barrios = df.groupby('neighbourhood_group')['price'].median().sort_values().index

# VISUALIZACIÓN : RIDGE PLOT
# Inspiración: Análisis de distribución de ingresos del NYT

fig_ridge = go.Figure()

colors = px.colors.qualitative.Bold  # Paleta de colores fuertes

for i, barrio in enumerate(orden_barrios):
    datos_barrio = df[df['neighbourhood_group'] == barrio]['price']

    fig_ridge.add_trace(go.Violin(
        x=datos_barrio,
        name=barrio,
        side='positive', # Solo muestra la parte de arriba (montaña)
        orientation='h', # Horizontal
        width=1.8,       # Ancho para que se solapen un poco (efecto 3D)
        points=False,    # Sin puntos para que sea limpio
        line_color='white',
        fillcolor=colors[i % len(colors)],
        opacity=0.7
    ))

fig_ridge.update_layout(
    title_text=" El Paisaje de Precios: Ridge Plot",
    title_font_size=20,
    xaxis_title="Precio por Noche (€)",
    yaxis_title="",
    template="plotly_dark",
    showlegend=False,
    height=700,
    bargap=0.1
)

# VISUALIZACIÓN 2: MAPA HEXAGONAL (DENSIDAD)
# Inspiración: Uber Engineering Blog

fig_hex = px.density_mapbox(
    df,
    lat='latitude',
    lon='longitude',
    z='price',
    radius=15, # Radio del hexágono/mancha
    center=dict(lat=41.39, lon=2.16),
    zoom=11,
    mapbox_style="carto-darkmatter",
    title=" Mapa de Densidad de Precios",
    color_continuous_scale="Viridis",
    height=600
)

# resultados
print("Generando visualizaciones inspiradas en Data Journalism...")
fig_ridge.show()
fig_hex.show()

Generando visualizaciones inspiradas en Data Journalism...


In [5]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
from google.colab import drive



# Limpieza
df['price'] = pd.to_numeric(df['price'].astype(str).str.replace(r'[$,]', '', regex=True), errors='coerce')
df = df.dropna(subset=['price', 'latitude', 'longitude', 'room_type'])
df = df[df['price'].between(10, 500)] # Filtro para enfocar el análisis

#  GENERAR CLUSTERS INTELIGENTES
# Usamos: Ubicación (Lat, Lon) + Precio
X = df[['latitude', 'longitude', 'price']]
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

kmeans = KMeans(n_clusters=5, random_state=42, n_init=10)
df['Cluster'] = kmeans.fit_predict(X_scaled)

# ANÁLISIS DEL "POR QUÉ" (Perfilado de Clusters)
# Calculamos métricas clave para explicar los precios
perfil = df.groupby('Cluster').agg({
    'price': 'mean',
    'number_of_reviews': 'mean',
    'room_type': lambda x: (x == 'Entire home/apt').mean() * 100 # % de aptos enteros
}).reset_index()
perfil.columns = ['Cluster', 'Precio Medio (€)', 'Popularidad (Reviews)', '% Apto. Entero']
perfil['Cluster'] = 'Grupo ' + perfil['Cluster'].astype(str)

# Ordenamos por precio para que el gráfico tenga sentido
perfil = perfil.sort_values('Precio Medio (€)', ascending=True)

#  VISUALIZACIÓN : MAPA DE CLUSTERS (DÓNDE)
fig_map = px.scatter_mapbox(
    df,
    lat="latitude",
    lon="longitude",
    color=df['Cluster'].astype(str),
    hover_data=['price', 'neighbourhood'],
    title=" Mapa de Clusters Económicos: ¿Dónde está el dinero?",
    mapbox_style="carto-darkmatter",
    zoom=11,
    height=600,
    color_discrete_sequence=px.colors.qualitative.Pastel # Colores distintivos
)

#  VISUALIZACIÓN: EL "POR QUÉ" (Doble Eje)
# Combinamos Precio (Barras) y Privacidad (Línea) para explicar la correlación
fig_reason = go.Figure()

# Barras: Precio
fig_reason.add_trace(go.Bar(
    x=perfil['Cluster'],
    y=perfil['Precio Medio (€)'],
    name='Precio Medio (€)',
    marker_color='indianred',
    opacity=0.8
))

# Línea: % de Apartamentos Enteros (Eje secundario)
fig_reason.add_trace(go.Scatter(
    x=perfil['Cluster'],
    y=perfil['% Apto. Entero'],
    name='% Privacidad (Apto. Entero)',
    yaxis='y2',
    line=dict(color='white', width=4),
    mode='lines+markers'
))

fig_reason.update_layout(
    title=" Explicación del Precio: Relación con la Privacidad",
    template="plotly_dark",
    yaxis=dict(title="Precio Medio (€)", side="left"),
    yaxis2=dict(title="% Apartamentos Enteros", side="right", overlaying="y", range=[0, 100]),
    legend=dict(x=0.01, y=0.99),
    height=500
)

# MOSTRAR
print("Generando análisis de Clusters...")
fig_map.show()
fig_reason.show()

Generando análisis de Clusters...
